In [1]:
import faiss
import pyterrier as pt
import ujson
import numpy as np

import itertools
import threading
import queue

from colbert.modeling.inference import ModelInference
from colbert.evaluation.loaders import load_colbert
from pyterrier_colbert import load_checkpoint
# monkeypatch to use our downloading version
import colbert.evaluation.loaders

colbert.evaluation.loaders.load_checkpoint = load_checkpoint
colbert.evaluation.loaders.load_model.__globals__['load_checkpoint'] = load_checkpoint
from colbert.utils.utils import print_message
import pickle
from colbert.indexing.index_manager import IndexManager
from warnings import warn
from transformers import AutoTokenizer, AutoModelForMaskedLM


In [2]:
pt.init()

PyTerrier 0.10.0 has loaded Terrier 5.8 (built by craigm on 2023-11-01 18:05) and terrier-helper 0.0.8

No etc/terrier.properties, using terrier.default.properties for bootstrap configuration.


In [3]:
from pyterrier_colbert.preprocessing import DatasetPreprocessor, TokenRemover, HFTokenizer, NLTKTokenizer

In [4]:
class Object():
    pass

In [5]:
checkpoint="http://www.dcs.gla.ac.uk/~craigm/colbert.dnn.zip"

In [6]:
args = Object()
args.similarity = 'cosine'
args.dim = 128
args.query_maxlen = 32
args.doc_maxlen = 180
args.checkpoint = checkpoint
args.mask_punctuation = False

In [7]:
dataset = pt.get_dataset('vaswani')

In [8]:
wordpiece = AutoTokenizer.from_pretrained("google-bert/bert-base-uncased")
hf_tokenizer = HFTokenizer(tokenizer=wordpiece)
nltk_tokenizer = NLTKTokenizer(tokenizer_type='treebank')

In [9]:
en_remover = TokenRemover(tokenizer=nltk_tokenizer, stopwords_files=['stopwords/stopwords-en.txt'])
en2_remover = TokenRemover(tokenizer=nltk_tokenizer, stopwords_files=['stopwords/stopwords-en.txt'], stopword_max_length=2)
en4_remover = TokenRemover(tokenizer=nltk_tokenizer, stopwords_files=['stopwords/stopwords-en.txt'], stopword_max_length=4)
en_punc_remover = TokenRemover(tokenizer=nltk_tokenizer, stopwords_files=['stopwords/stopwords-en.txt', 'stopwords/stopwords-punctuations.txt'])
lim_remover = TokenRemover(tokenizer=nltk_tokenizer, stopwords_files=['stopwords/stopwords-limited.txt'])
lim_punc_remover = TokenRemover(tokenizer=nltk_tokenizer, stopwords_files=['stopwords/stopwords-limited.txt', 'stopwords/stopwords-punctuations.txt'])

In [10]:
en2_remover.stopwords = en2_remover.stopwords | set(['the'])

In [12]:
cleaners = [('en', en_remover),('en2', en2_remover),('en4', en4_remover) ,('few', lim_remover)]

In [13]:
datasets_cleaned = {name: DatasetPreprocessor(dataset=dataset, tokenizer=wordpiece, preprocessor=cleaner) for name, cleaner in cleaners}

In [14]:
lx = 0
for doc in datasets_cleaned['few']:
    lx = lx + len(doc['text'])
    print(doc)

{'text': 'compact memories have flexible capacities digital data storage system with capacity up bits and random and or sequential access described', 'docno': '1'}
{'text': 'electronic analogue computer for solving systems linear equations mathematical derivation operating principle and stability conditions for computer consisting amplifiers', 'docno': '2'}
{'text': 'electronic coordinate transformer circuit details given for construction electronic calculating unit which enables polar coordinates vector modulus and cosine or sine argument be derived from those rectangular system axes', 'docno': '3'}
{'text': 'british computer society report conference held cambridge june', 'docno': '4'}
{'text': 'millimicrosecond digital computer logic system fast pulse logic described which combines efficiency transformer coupled stages with digit delay tolerances approaching that dc coupled systems logical circuits for or and inverter and reclock shown together with driver which permits fan out fact

{'text': 'approximation errors diode function generators errors resulting from fitting piecewise linear function smooth curve discussed relation analogue computor applications simple integral based best fis criteria will give relation between number segments and error and also breakpoints between segments numerical results given for typical functions', 'docno': '400'}
{'text': 'theoretical study and method operation logarithmic integrator description computer circuit based diode pump action', 'docno': '401'}
{'text': 'construction digital computing system from basic transistor circuit computer uses identical basic circuits convert decimal numbers and from binary scale diagrams basic circuit and system given printed circuits used', 'docno': '402'}
{'text': 'light pen links computer operator using photodiode read dots produced tube enables operator control associated computer pointing light pen certain dots information can be written into computer', 'docno': '403'}
{'text': 'computers ai

{'text': 'stabilization magnetic field electromagnet system described for controlling both rapid and slow variations magnetic field means transistorized control stage and feedback winding slow variations detected magnetic resonance protons ferric nitrate solution using technique similar that described earlier', 'docno': '918'}
{'text': 'precision thermostat temperature sensitive resistance bridge controls crystal oven give short period temperature stability', 'docno': '919'}
{'text': 'stable thermostat for measurement noise and drift semiconductor circuit elements rectified output bridge circuit containing resistance thermometer used control heating stirred oil bath noise voltage transistors power supply circuit and zener reference diode have been measured very low and audio frequencies using apparatus described', 'docno': '920'}
{'text': 'experimental impedance relay using hall effect semiconductor description definite impedance relay for protection power transmission systems hall out

{'text': 'image parameter theory for mechanical quadripoles compressional or torsional oscillation equivalence parameters mechanical system transmitting compressional or torsional oscillations and parameters electrical transmission line established design mechanical filters described and design formulae with response characteristics given for basic filter sections', 'docno': '1474'}
{'text': 'special band pass half sections design crystal filters branch network type described', 'docno': '1475'}
{'text': 'decimal attenuator network combining properties conventional voltage or current divider with those constant resistance attenuator', 'docno': '1476'}
{'text': 'multiple isolated input metoork with common output design equations developed for general case n isolated inputs with common output measurements made two input and three input units given', 'docno': '1477'}
{'text': 'frequency three phase rc coupled oscillator part two inductive anode load resistance', 'docno': '1478'}
{'text': '

{'text': 'helical coordinate system and its applications electromagnetic theory system described enables problems involving helical symmetry be solved exactly', 'docno': '1891'}
{'text': 'edge condition diffraction problems diffraction em wave perfectly conducting solid considered', 'docno': '1892'}
{'text': 'theory wave scattering periodically uneven surfaces description six approximate mathematical methods for calculating scattering sound or em waves over sea or uneven ground references', 'docno': '1893'}
{'text': 'magnetic double refraction microwaves paramagnetics investigation rotation plane polarization wave circular waveguide containing paramagnetic salt and its dependence intensity static magnetic field perpendicular direction wave propagation', 'docno': '1894'}
{'text': 'spin wave analysis ferromagnetic resonance polycrystalline ferrites dipolar interaction taken into account means spin wave formalism crystalline anisotropy and polycrystalline nature material cause homogeneous

...

{'text': 'relation between intensity distributions over radiating systems and their directivity characteristics fourier transform analysis used show that contrary fischers result directivity characteristic linear or plane radiator finite dimensions uniquely related amplitude distribution over radiator theory extended consideration propagation media with local inhomogeneities acting secondary radiators and investigation made relation between distribution inhomogeneities and directivity characteristic scattered radiation', 'docno': '8383'}
{'text': 'study electromagnetic field vicinity reflecting surface analysis given for general case plane incident wave with elliptical polarization if reflecting surface infinite plane reflected wave also plane modifications reflected wave other types reflecting surface mentioned', 'docno': '8384'}
{'text': 'simultaneous partial absorption reflection and transmission nonuniform plane wave thin metal film theory developed for uniform waves extended nonun

{'text': 'interaction terrestrial magnetic field with solar corpuscular radiation shape cavity between earth and neutral solar stream differs only from hemisphere radius earth radii incident side but elongated other side distance order earth radii cavity idented polar latitudes where current layer reverses', 'docno': '9024'}
{'text': 'cause magnetic storms and bays circulating currents set up around regions proton and electron precipitation hall effect suggested cause magnetic bays and storms', 'docno': '9025'}
{'text': 'daytime enhancement amplitude geomagnetic sudden impulses equatorial region igy data from equatorial stations provide some evidence that sudden impulses and sudden commencements caused similar mechanisms', 'docno': '9026'}
{'text': 'evidence quasi perpendicular propagation hydromagnetic waves caused nuclear explosions over johnston island', 'docno': '9027'}
{'text': 'verification earths pear shape gravitational harmonic errors predictions orbit transit ib satellite acc

{'text': 'effect series resistance photovoltaic solar energy conversion series resistance photovoltaic cell divided into two components contact and sheet resistance each components examined theoretically and experimentally and qualitative agreement between theory and experiment shown it concluded that contact resistance reduces conversion efficiency more than sheet resistance', 'docno': '9664'}
{'text': 'considerations photoemissive energy converters efficiency o solar energy converter consisting emitter and ag collector calculated taking into account initial velocities photoelectrons but ignoring space charge efficiencies between and obtained for output voltages between and efficiency increases percentage blue and ultraviolet radiation source increased minimize space charge effects emitter collector spacing must be order or less', 'docno': '9665'}
{'text': 'optimum capacitor charging efficiency for space systems several theorems for perfect time shaped source voltages which optimize e

{'text': 'average forces electromagnetic systems for ar linear and loss free system it shown that time average force can be expressed directly measurable circuit theory parameters', 'docno': '10231'}
{'text': 'supplement study electromagnetic point point sources supplement previously published paper establishing that there only two fundamental fields which can effectively be replaced point source corresponding distribution concentric about its origin', 'docno': '10232'}
{'text': 'cherenkov radiation for dipole moment medium with spatial dispersion treatment electric and magnetic dipoles isotropic nongyrotropic medium radiation from ring current such medium also considered', 'docno': '10233'}
{'text': 'radiation charged particles passing through electron plasma external magnetic field coupling between longitudinal plasma wave and transverse em wave modifies nature radiation particle velocities greater than that required for excitation plasma waves non cherenkov type radiation will occur

{'text': 'radiation from modulated electron beam with plasma background expressions derived for electromagnetic radiation current modulated electron beams which emerge from plasma simple expressions derived case where dielectric constant plasma zero or infinity', 'docno': '10924'}
{'text': 'diffraction electromagnetic wates sound waves diffraction amplitude calculated from borns approximation results measurements microwaves affected standing sound frequency and polarization em waves', 'docno': '10925'}
{'text': 'transmission and reflection electromagnetic waves plasma boundary for arbitrary angles incidence plane em wave horizontally or vertically polarized incident arbitrary angle flat plasma boundary investigated numerical results showing variation attenuation and phase power entering plasma and ellipticity reflected wave presented', 'docno': '10926'}
{'text': 'some features transverse propagation high frequency waves magneto active plasma mathematical analysis based kinetic equation

In [15]:
lx

2649415

In [16]:
ly = 0
for doc in datasets_cleaned['en2']:
    ly = ly + len(doc['text'])
    print(doc)

{'text': 'compact memories have flexible capacities digital data storage system with capacity bits and random and sequential access described', 'docno': '1'}
{'text': 'electronic analogue computer for solving systems linear equations mathematical derivation operating principle and stability conditions for computer consisting amplifiers', 'docno': '2'}
{'text': 'electronic coordinate transformer circuit details are given for construction electronic calculating unit which enables polar coordinates vector modulus and cosine sine argument derived from those rectangular system axes', 'docno': '3'}
{'text': 'british computer society report conference held cambridge june', 'docno': '4'}
{'text': 'millimicrosecond digital computer logic system fast pulse logic described which combines efficiency transformer coupled stages with digit delay tolerances approaching that dc coupled systems logical circuits for and inverter and reclock are shown together with driver which permits fan out factor tran

{'text': 'model phosphors basis quantum mechanics transition probabilities with constant defects and discrete spectrum', 'docno': '52'}
{'text': 'quantum mechanical theory dielectric orientation polarization gases orientation dipolar gas consisting symmetric spin molecules attenuating electric field', 'docno': '53'}
{'text': 'influence thomson effect relationship for constrictive resistance thermal equilibrium', 'docno': '54'}
{'text': 'investigation highfrequency resonant discharge experimental study discharge magnetic field frequency range theoretical and experimental analysis made breakdown conditions and characteristics and properties plasma discharge', 'docno': '55'}
{'text': 'application schottkys diffusion theory discharges with several types ions and excited neutral particles', 'docno': '56'}
{'text': 'low pressure plane symmetric discharge', 'docno': '57'}
{'text': 'pulse technique for probe measurements gas discharges', 'docno': '58'}
{'text': 'frequency multiplication second

{'text': 'image parameter theory simple aid realization crystal band pass filters branch network type design formulae and curves are given for ladder type networks with crystal shunt arms', 'docno': '654'}
{'text': 'new coaxial resonator filter band pass filter with derived type characteristic described consisting loop coupled coaxial resonators reentrant arrangement performance may described terms equivalent lattice network good agreement shown between experimental and theoretical insertion loss characteristics', 'docno': '655'}
{'text': 'analysis active networks admittance matrices admittance matrices valves and transistors are derived directly and from their indefinite admittance matrices', 'docno': '656'}
{'text': 'considerations oscillator stability methods reducing microphony effects and temperature dependence oscillators television tuners', 'docno': '657'}
{'text': 'procedure for tuning bridge stabilized crystal oscillator meacham bridge circuit used which lamp replaced thermist

{'text': 'note diffraction infinite slit previous results for plane waves longer wavelengths are extended obtain transmission coefficients oblique angles incidence cylindrical waves are considered briefly', 'docno': '717'}
{'text': 'diffraction spheroid diffracted field determined two methods for wavelengths small compared spheroid results are applied evaluate back scattered fields', 'docno': '718'}
{'text': 'investigations artificial dielectrics microwave frequencies part two expression for phase change transmission wave incident parallel plate type artificial dielectric function plate spacing has been verified experimentally', 'docno': '719'}
{'text': 'reflection electromagnetic waves from medium excited acoustic waves theory developed for variation density and temperature liquid caused acoustic wave generating regions maximum and minimum dielectric constant modulation wave reflected from acoustically disturbed water surface observed', 'docno': '720'}
{'text': 'confinement charged pa

{'text': 'resolving time and flipping time magnetoresistive flip flops time constant exponential approach stable states shown fair approximation for flipping time bridge type magnetoresistive flip flop order for materials present available method calculating flipping time extended more general networks and dependence flipping time incoming pulse considered', 'docno': '1329'}
{'text': 'impulse governed oscillator techniques part one general principles techniques are discussed special circuits and theoretical data will given subsequent issues', 'docno': '1330'}
{'text': 'monochromaticity and noise regenerative electrical oscillator expressions are derived for departure from monochromaticity regenerative oscillator represented equivalent rlc circuit haing negative resistance parallel with intensity and band width thermal noise generated oscillator resistance are also considered', 'docno': '1331'}
{'text': 'frequency stability stable multivibrators using transistors dependence multivibrato

...

{'text': 'some studies bifurcation ionospheric layer into and ionograms recorded frequent intervals cambridge and show how layers develop sunrise quiet and disturbed days and different seasons', 'docno': '8922'}
{'text': 'pre sunrise phenomenon and presence negative ions region ionosphere increases layer electron density which occur about two hours before ground sunrise might due photodetachment electrons from negative ions', 'docno': '8923'}
{'text': 'test procedure for easy estimation representative monthly electron density profiles for ionosphere profile produced from mean daily virtual height curves well within one standard deviation mean individual profiles', 'docno': '8924'}
{'text': 'study observed spread examination large number ionograms shows effect using different receiver gain settings and reveals night phenomenon degree spreading varies with magnetic dip', 'docno': '8925'}
{'text': 'possible importance nitric oxide formation during polar cap ionospheric absorption events p

{'text': 'penetration microwaves into rarer medium total reflection using right angle prisms separated narrow air gap transmission and reflection coefficients paraffin sulphur and have bee measured function gap width', 'docno': '9466'}
{'text': 'refraction and diffraction pulses solution for reflection and refraction plane pulse plane surface obtained fourier synthesis using method which also valid when total reflection occurs', 'docno': '9467'}
{'text': 'spectrometer for paramagnetic electron resonance with different methods detection equipment described can used for klystron frea spectrometer for paramagnetic electron resonance with different methods detection equipment described can used for klystron frequency modulation and magnetic sweep methods measurement', 'docno': '9468'}
{'text': 'theory ferro and antiferromagnetic resonance absorption', 'docno': '9469'}
{'text': 'longitudinal ferrimagnetic resonance susceptibility components are calculated for triangular ferrimagnetic system

{'text': 'surface distributions fixed charges and poynting vector system permanent volume currents theoretical study conditions hollow cylindrical conductor', 'docno': '9972'}
{'text': 'present state theory electric breakdown solid dielectrics survey theory first stage dielectric breakdown loss electric strength can probably given best terms kinetic equation for electrons solid effective cross sections ionization for low energy electrons probability scattering medium energy electrons vibrating lattice and effective cross section recombination must determined theory second stage actual breakdown has not yet been given suggested that cause breakdown could connected with processes leading production shock wave analogous that occurring breakdown gases high pressures references include over russian literature', 'docno': '9973'}
{'text': 'mechanism discharge between plane plates problem considered using diffusion theory positive column with term added take account character discharge measure

{'text': 'radar boxcar circuits suing nuvistors transistors and zeners two versions waveform sampling device with zener diode biasing are described which give signal noise ratio room temperature', 'docno': '10633'}
{'text': 'amplifiers with band filter coupling design multistage amplifiers with flat tchebycheff type response considered design formulae and response cuf curves are given', 'docno': '10634'}
{'text': 'transistor amplifier stages with prescribed gain and sensitivity design procedure developed for circuits meeting prescribed gain and sensitivity criteria terms anticipated operational variations and available component data', 'docno': '10635'}
{'text': 'engineering approach design transistor feedback amplifiers technique developed for amplifier design which produces very accurate expressions for transmittance without requiring any quantitative information about transistors', 'docno': '10636'}
{'text': 'dielectric harmonic amplifier controllable harmonic generator circuits inc

{'text': 'influence differential transformer attenuation characteristic differential bridge filters', 'docno': '11314'}
{'text': 'duality nonplanar electric circuits without use ideal transformers method constructing dual any linear lumped nonplanar network which does not include magnetic coupling given without using ideal transformers', 'docno': '11315'}
{'text': 'hall effect microwave mixer signal frequency current and magnetic field local oscillator frequency produce hall effect emf across semiconducting plate minimum conversion loss achieved', 'docno': '11316'}
{'text': 'survey very low frequency oscillators methods generating frequencies below for vibration work and for testing servomechanisms are outlined major characteristics instruments are tabulated', 'docno': '11317'}
{'text': 'high stability transistor oscillator for design development construction and testing oscillator are described power output stable within and frequency within ove temperature range', 'docno': '11318'}
{

In [17]:
import pyterrier_colbert.indexing
import torch
import os

In [18]:
ly

2649949

In [19]:
if not os.path.exists('./indexes/index.base.vaswani/'):
    base_indexer = pyterrier_colbert.indexing.ColBERTIndexer(checkpoint, "./indexes", "index.base.vaswani", chunksize=3, num_partitions=512)
    base_indexer.index(dataset.get_corpus_iter(), )

In [20]:
clean_indexers = {}
for name, data_iter in datasets_cleaned.items():
    if not os.path.exists(f'./indexes/index.clean.{name}.vaswani/'):
        cleaned_indexer = pyterrier_colbert.indexing.ColBERTIndexer(checkpoint, f'./indexes', f'index.clean.{name}.vaswani', chunksize=3, num_partitions=256)
        cleaned_indexer.index(data_iter)
        clean_indexers[name] = cleaned_indexer
        clean_indexer = None
        torch.cuda.empty_cache()

[Mar 04, 17:11:31] [0] 		 #> Local args.bsize = 128
[Mar 04, 17:11:31] [0] 		 #> args.index_root = ./indexes
[Mar 04, 17:11:31] [0] 		 #> self.possible_subset_sizes = [69905]


Some weights of ColBERT were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['linear.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


[Mar 04, 17:11:34] #> Loading model checkpoint.
[Mar 04, 17:11:34] #> Loading checkpoint http://www.dcs.gla.ac.uk/~craigm/colbert.dnn.zip


/home/busolin/miniconda3/envs/cleanbert/lib/python3.8/site-packages/torch/hub.py:513: UserWarning: Falling back to the old format < 1.6. This support will be deprecated in favor of default zipfile format introduced in 1.6. Please redo torch.save() to save it in the new zipfile format.
  warnings.warn('Falling back to the old format < 1.6. This support will be '


[Mar 04, 17:11:42] #> checkpoint['epoch'] = 0
[Mar 04, 17:11:42] #> checkpoint['batch'] = 44500




[Mar 04, 17:11:43] #> Note: Output directory ./indexes already exists




[Mar 04, 17:11:43] #> Creating directory ./indexes/index.clean.en.vaswani 


[Mar 04, 17:13:41] [0] 		 #> Completed batch #0 (starting at passage #0) 		Passages/min: 5.8k (overall),  6.0k (this encoding),  7690.4M (this saving)
[Mar 04, 17:13:41] [0] 		 [NOTE] Done with local share.
[Mar 04, 17:13:41] [0] 		 #> Joining saver thread.
[Mar 04, 17:13:41] [0] 		 #> Saved batch #0 to ./indexes/index.clean.en.vaswani/0.pt 		 Saving Throughput = 4.4M passages per minute.

#> num_embeddings = 341244
[Mar 04, 17:13:41] #> Starting..
[Mar 04, 17:13:41] #> Processing slice #1 of 1 (range 0..1).
[Mar 04, 17:13:41] #> Will write to ./indexes/index.clean.en.vaswani/ivfpq.256.faiss.
[Mar 04, 17:13:41] #> Loading ./indexes/index.clean.en.vaswani/0.sample ...
#> Sample has shape (17062, 128)
[Mar 04, 17:13:41] Preparing resources f

Some weights of ColBERT were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['linear.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


[Mar 04, 17:13:56] #> Loading model checkpoint.
[Mar 04, 17:13:56] #> Loading checkpoint http://www.dcs.gla.ac.uk/~craigm/colbert.dnn.zip
[Mar 04, 17:14:03] #> checkpoint['epoch'] = 0
[Mar 04, 17:14:03] #> checkpoint['batch'] = 44500




[Mar 04, 17:14:04] #> Note: Output directory ./indexes already exists




[Mar 04, 17:14:04] #> Creating directory ./indexes/index.clean.en2.vaswani 


[Mar 04, 17:16:07] [0] 		 #> Completed batch #0 (starting at passage #0) 		Passages/min: 5.6k (overall),  5.8k (this encoding),  7629.2M (this saving)
[Mar 04, 17:16:07] [0] 		 [NOTE] Done with local share.
[Mar 04, 17:16:07] [0] 		 #> Joining saver thread.
[Mar 04, 17:16:07] [0] 		 #> Saved batch #0 to ./indexes/index.clean.en2.vaswani/0.pt 		 Saving Throughput = 3.4M passages per minute.

#> num_embeddings = 442442
[Mar 04, 17:16:07] #> Starting..
[Mar 04, 17:16:07] #> Processing slice #1 of 1 (range 0..1).
[Mar 04, 17:16:07] #> Will write to ./indexes/index.clean.en2.vaswani/ivfpq.256.faiss.
[Mar 04,

Some weights of ColBERT were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['linear.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


[Mar 04, 17:16:25] #> Loading model checkpoint.
[Mar 04, 17:16:25] #> Loading checkpoint http://www.dcs.gla.ac.uk/~craigm/colbert.dnn.zip
[Mar 04, 17:16:32] #> checkpoint['epoch'] = 0
[Mar 04, 17:16:32] #> checkpoint['batch'] = 44500




[Mar 04, 17:16:33] #> Note: Output directory ./indexes already exists




[Mar 04, 17:16:33] #> Creating directory ./indexes/index.clean.en4.vaswani 


[Mar 04, 17:18:35] [0] 		 #> Completed batch #0 (starting at passage #0) 		Passages/min: 5.6k (overall),  5.8k (this encoding),  8637.2M (this saving)
[Mar 04, 17:18:35] [0] 		 [NOTE] Done with local share.
[Mar 04, 17:18:35] [0] 		 #> Joining saver thread.
[Mar 04, 17:18:35] [0] 		 #> Saved batch #0 to ./indexes/index.clean.en4.vaswani/0.pt 		 Saving Throughput = 4.2M passages per minute.

#> num_embeddings = 378275
[Mar 04, 17:18:35] #> Starting..
[Mar 04, 17:18:35] #> Processing slice #1 of 1 (range 0..1).
[Mar 04, 17:18:35] #> Will write to ./indexes/index.clean.en4.vaswani/ivfpq.256.faiss.
[Mar 04,

In [21]:
print('gg')

gg
